In [2]:
import datetime as dt

import matplotlib.pyplot as plt
import mplfinance as mpf
import numpy as np
import pandas as pd
import pandas_market_calendars as mcal
import plotly.graph_objects as go
import polars as pl
from dash import Dash, dcc, html
from plotly.subplots import make_subplots

nse = mcal.get_calendar("NSE")

pd.set_option("display.max_rows", 25_000)
pd.set_option("display.max_columns", 500)
pl.Config.set_tbl_cols(500)
pl.Config.set_tbl_rows(10_000)

pd.options.display.float_format = "{:.4f}".format

import sys

sys.path.append("..")
from fetching_from_local_db.enums import AssetClass, Index, StrikeSpread
from fetching_from_local_db.fetch_from_db import (
    _fetch_batch,
    fetch_data,
    fetch_spot_data,
)
from tooling.enums import AssetClass, Index, Spot, StrikeSpread
from tooling.fetch import fetch_option_data, fetch_spot_data
from tooling.filter import find_atm, option_tool

In [3]:
async def get_expiry(f_today, symbol):
    if symbol == 'bnf':
        if (f_today <= dt.date(2024, 1, 25)) and (f_today >= dt.date(2024, 1, 18)):
            f_expiry = dt.date(2024, 1, 25)
        elif (f_today <= dt.date(2024, 1, 31)) and (f_today >= dt.date(2024, 1, 26)):
            f_expiry = dt.date(2024, 1, 31)
        elif (f_today <= dt.date(2024, 2, 22)) and (f_today >= dt.date(2024, 2, 29)):
            f_expiry = dt.date(2024, 2, 29)
        elif (f_today <= dt.date(2024, 3, 25)) and (f_today >= dt.date(2024, 3, 27)):
            f_expiry = dt.date(2024, 2, 27)
        elif f_today < dt.date(2023, 9, 1):
            days_to_thursday = (3 - f_today.weekday()) % 7
            nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
            f_expiry = nearest_thursday
            if nse.valid_days(start_date=nearest_thursday, end_date=nearest_thursday).empty:
                f_expiry = nearest_thursday - dt.timedelta(days=1)
        elif f_today >= dt.date(2023, 9, 1):
            if f_today.day < 24:
                days_to_wednesday = (2 - f_today.weekday()) % 7
                nearest_wednesday = f_today + dt.timedelta(days=days_to_wednesday)
                f_expiry = nearest_wednesday
                if nse.valid_days(
                    start_date=nearest_wednesday, end_date=nearest_wednesday
                ).empty:
                    f_expiry = nearest_wednesday - dt.timedelta(days=1)
            else:
                days_to_thursday = (3 - f_today.weekday()) % 7
                nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
                f_expiry = nearest_thursday
                if nse.valid_days(
                    start_date=nearest_thursday, end_date=nearest_thursday
                ).empty:
                    f_expiry = nearest_thursday - dt.timedelta(days=1)
        return f_expiry
    elif symbol == 'nifty':
        days_to_thursday = (3 - f_today.weekday()) % 7
        nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
        f_expiry = nearest_thursday
        if nse.valid_days(start_date=nearest_thursday, end_date=nearest_thursday).empty:
            f_expiry = nearest_thursday - dt.timedelta(days=1)
        return f_expiry

    elif symbol == 'fnf':
        days_to_thursday = (1 - f_today.weekday()) % 7
        nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
        f_expiry = nearest_thursday
        if nse.valid_days(start_date=nearest_thursday, end_date=nearest_thursday).empty:
            f_expiry = nearest_thursday - dt.timedelta(days=1)
        return f_expiry

    elif symbol == 'midcp':
        days_to_thursday = (0 - f_today.weekday()) % 7
        nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
        f_expiry = nearest_thursday
        if nse.valid_days(start_date=nearest_thursday, end_date=nearest_thursday).empty:
            f_expiry = nearest_thursday - dt.timedelta(days=1)
        return f_expiry

    else:
        return 0

In [4]:
bnf_pandas = pd.read_csv("../data/nifty.csv")

In [5]:
# If Stocks Data ...
bnf_pandas["datetime"] = pd.to_datetime(bnf_pandas["datetime"])
bnf_pandas["datetime"] = bnf_pandas["datetime"].dt.tz_localize(None)
bnf_pandas = bnf_pandas[bnf_pandas["datetime"].dt.year >= 2019]
# bnf_pandas.drop(columns=["time"], inplace=True)
# bnf_pandas

In [6]:
bnf = pl.DataFrame(bnf_pandas)
print(type(bnf))
# bnf

<class 'polars.dataframe.frame.DataFrame'>


In [7]:
bnf = bnf.with_columns([pl.col("datetime").alias("index")]).drop("datetime")
bnf = bnf.with_columns(pl.col("index").alias("datetime"))

In [8]:
def resample(
    data: pl.DataFrame, timeframe, offset: dt.timedelta | None = None
) -> pl.DataFrame:
    return (
        data.set_sorted("datetime")
        .group_by_dynamic(
            index_column="datetime",
            every=timeframe,
            period=timeframe,
            label="left",
            offset=offset,
        )
        .agg(
            [
                pl.col("o").first().alias("o"),
                pl.col("h").max().alias("h"),
                pl.col("l").min().alias("l"),
                pl.col("c").last().alias("c"),
                pl.col("v").sum().alias("v"),
            ]
        )
    )

In [9]:
# bnf = bnf.with_columns(pl.col('datetime').str.strptime(pl.Datetime, "%Y-%m-%d %H:%M:%S"))
# bnf = bnf.filter(pl.col('datetime').dt.year() >= 2019)
# print(bnf.tail())

In [10]:
# INDEX = 'MIDCP'
# INDEX = 'BNF'
INDEX = 'NIFTY'
# INDEX = 'FNF'
# INDEX = 'STOCK'
# INDEX = 'SENSEX'

portfolio_ = 10000000

if INDEX == 'BNF':
    lev_ = 5
    index_ = 'banknifty'
    slippage_ = 0.01
    lot_size_ = 15
    spread_ = 100
elif INDEX == 'NIFTY':
    lev_ = 6
    index_ = 'nifty'
    slippage_ = 0.01
    lot_size_ = 25
    spread_ = 50
elif INDEX == 'FNF':
    lev_ = 6
    index_ = 'finnifty'
    slippage_ = 0.01
    lot_size_ = 25
    spread_ = 50
elif INDEX == 'MIDCP':
    lev_ = 8
    index_ = 'midcpnifty'
    slippage_ = 0.01
    lot_size_ = 50
    spread_ = 25
elif INDEX == 'SENSEX':
    lev_ = 7
    index_ = 'sensex'
    slippage_ = 0.01
    lot_size_ = 10
    spread_ = 100
elif INDEX == 'STOCK':
    lev_ = 5
    slippage_ = 0.01
    lot_size_ = 1


In [23]:
def generate_reversal_signals(df, fast_ma, slow_ma):
    
    df['c'] = pd.to_numeric(df['c'], errors='coerce')
    close_prices = df['c']
    
    fast_ema = close_prices.ewm(span=fast_ma, adjust=False).mean()
    slow_ema = close_prices.ewm(span=slow_ma, adjust=False).mean()

    macd = slow_ema - fast_ema
    # prev_macd = macd.shift(1)
    
    df['macd'] = macd
    # df['prev_macd'] = prev_macd

    df.loc[(df['macd'].shift(1) >= df['macd']) & (df['macd'].shift(1) > 0), 'reversal_signal'] = True
    
    return df

In [24]:
def manage_trade(data, entry_price, trailing_stop_loss=None):
    """Manage trade by updating trailing stop-loss and exiting at the end of the day."""
    exit_price = None
    for _, row in data.iterrows():
        if trailing_stop_loss is None or row['close'] < trailing_stop_loss:
            trailing_stop_loss = row['MA_20']  # Update stop-loss with MA
        
        # Square off at 15:15
        if row['time'].time() == datetime(2024, 12, 8, 15, 15).time():
            exit_price = row['close']
            break
    return exit_price, trailing_stop_loss

In [25]:
# # Main function
# def run_strategy(start_date, end_date, index="NIFTY"):
#     tradebook = []
#     current_date = start_date
    
#     while current_date <= end_date:
#         # Fetch the spot value (replace with real data fetching logic)
#         spot_value = 19500  # Example spot value
#         atm_strike = get_atm_strike(spot_value)
#         expiry = get_next_thursday(current_date)

#         start_time = datetime.combine(current_date, datetime.min.time()) + timedelta(hours=9, minutes=15)
#         end_time = datetime.combine(current_date, datetime.min.time()) + timedelta(hours=15, minutes=15)

#         # Fetch data for ATM call and put options
#         call_data = fetch_data(index=index, strike=atm_strike, option_type="CE", expiry=expiry, start_datetime=start_time, end_datetime=end_time)
#         put_data = fetch_data(index=index, strike=atm_strike, option_type="PE", expiry=expiry, start_datetime=start_time, end_datetime=end_time)

#         # Generate signals
#         call_data = generate_signals(call_data)
#         put_data = generate_signals(put_data)

#         # Process trades for call options
#         if call_data['short_signal'].any():
#             entry_price = call_data.loc[call_data['short_signal'], 'close'].iloc[0]
#             exit_price, trailing_stop = manage_trade(call_data, entry_price)
#             tradebook.append({
#                 "date": current_date,
#                 "type": "CALL",
#                 "strike": atm_strike,
#                 "entry_price": entry_price,
#                 "exit_price": exit_price,
#                 "trailing_stop": trailing_stop
#             })

#         # Process trades for put options
#         if put_data['short_signal'].any():
#             entry_price = put_data.loc[put_data['short_signal'], 'close'].iloc[0]
#             exit_price, trailing_stop = manage_trade(put_data, entry_price)
#             tradebook.append({
#                 "date": current_date,
#                 "type": "PUT",
#                 "strike": atm_strike,
#                 "entry_price": entry_price,
#                 "exit_price": exit_price,
#                 "trailing_stop": trailing_stop
#             })
        
#         # Move to the next day
#         current_date += timedelta(days=1)

#     # Return tradebook as a DataFrame
#     return pd.DataFrame(tradebook)

# # Example usage
# start_date = datetime(2024, 12, 4)
# end_date = datetime(2024, 12, 8)
# tradebook = run_strategy(start_date, end_date)
# print(tradebook)

In [56]:
async def take_trade(ce_df, pe_df, ce_strike, pe_strike, expiry):
    """
    Function to process both CE and PE option dataframes for trades.

    Parameters:
    ce_df (DataFrame): DataFrame for CE option data.
    pe_df (DataFrame): DataFrame for PE option data.
    tradebook (DataFrame): DataFrame to store the trades.

    Returns:
    DataFrame: Updated tradebook containing all trades.
    """
    # Initialize tracking variables for CE and PE options
    ce_entry_low = None
    pe_entry_low = None
    ce_trade_active = False
    pe_trade_active = False
    in_trade_ce = False
    in_trade_pe = False
    ce_points = 0
    pe_points = 0
    exit_remark = None
    previous_row = None

    # Initialize a tradebook for each day's trades
    daily_trades = pd.DataFrame(columns=["option_type", "entry_price", "entry_time", "status", "stop_loss"])
    tradebook = []

    # Process CE dataframe
    for i, row in ce_df.iterrows():
        if previous_row is not None:
            previous_row = row
        # print(row['datetime'])
        if row['reversal_signal'] and not in_trade_ce:
            if row['l'] > 10:
                if ce_entry_low is None or row['l'] > ce_entry_low:
                    ce_entry_low = row['l']  # Update entry low price
                    # print(f"CE Reversal Signal: New low updated to {ce_entry_low}")

        if ce_entry_low is not None and row['l'] < ce_entry_low and not in_trade_ce:
            # Low break found, take the trade
            in_trade_ce = True
            entry_price = ce_entry_low
            entry_time = row['datetime']
            stop_loss = 1.5 * entry_price  # SL as 1.5 * entry_price
            ce_entry_low = None  # Reset entry low after trade is taken
            # print(f"CE Trade: Entry at {entry_price} on {entry_time}")

        if in_trade_ce:
            if row['c'] >= stop_loss:
                # SL Hit
                exit_price = row['c']
                exit_time = row['datetime']
                ce_points = entry_price - exit_price
                exit_remark = 'SL Hit'
                in_trade_ce = False

            elif (previous_row is not None) and (row['macd'] > previous_row['macd']):
                # MACD Reversal logic
                exit_price = row['c']
                exit_time = row['datetime']
                ce_points = entry_price - exit_price
                exit_remark = 'MACD Reversal'
                in_trade_ce = False
                # print(f"Exited at {exit_time} with {ce_points} points. Remark: {exit_remark}")
            

            elif row['datetime'].time() >= dt.time(15, 15):
                # EOD Exit
                exit_price = row['c']
                exit_time = row['datetime']
                ce_points = entry_price - exit_price
                exit_remark = 'EOD Exit'
                in_trade_ce = False

            elif row['l'] <= 1:
                # Decay Complete, Exit
                exit_price = 1
                exit_time = row['datetime']
                ce_points = entry_price - exit_price
                exit_remark = 'Target Hit'
                in_trade_ce = False

            # Update previous_row
            previous_row = row
            
        if ce_points:
            # print(exit_remark)
            qty = portfolio_ * lev_ / ce_strike
            slippages = (entry_price + exit_price) * slippage_
            trade = {
                'Strike': ce_strike,
                'Option Type': 'CE',
                'Expiry': expiry,
                'Portfolio': portfolio_,
                'Entry Time': entry_time,
                'Entry Price': entry_price,
                'Exit Time': exit_time,
                'Exit Price': exit_price,
                'Remark': exit_remark,
                'Points': ce_points,
                'Qty': qty,
                'PnL': ce_points * qty,
                'Slippages': slippages,
                'PnL w cs': (ce_points - slippages) * qty,
                'ROI%': (ce_points - slippages) * qty * 100 / portfolio_,
            }
            # print(trade)
            tradebook.append(trade)
            ce_points = 0
            exit_remark = None

    # Process PE dataframe
    for i, row in pe_df.iterrows():
        # print(row['datetime'])
        if row['reversal_signal'] and not in_trade_pe:
            if row['l'] > 10:
                if pe_entry_low is None or row['l'] > pe_entry_low:
                    pe_entry_low = row['l']  # Update entry low price
                    # print(f"PE Reversal Signal: New low updated to {pe_entry_low}")

        if pe_entry_low is not None and row['l'] < pe_entry_low and not in_trade_pe:
            # Low break found, take the trade
            entry_price = pe_entry_low
            entry_time = row['datetime']
            stop_loss = 1.5 * entry_price  # SL as 1.5 * entry_price
            pe_entry_low = None  # Reset entry low after trade is taken
            # print(f"PE Trade: Entry at {entry_price} on {entry_time}")
            in_trade_pe = True

        if in_trade_pe:
            if row['c'] >= stop_loss:
                # SL Hit
                exit_price = row['c']
                exit_time = row['datetime']
                pe_points = entry_price - exit_price
                exit_remark = 'SL Hit'
                in_trade_pe = False

            elif row['datetime'].time() >= dt.time(15, 15):
                # EOD Exit
                exit_price = row['c']
                exit_time = row['datetime']
                pe_points = entry_price - exit_price
                exit_remark = 'EOD Exit'
                in_trade_pe = False

            elif row['l'] <= 1:
                # Decay Complete, Exit
                exit_price = 1
                exit_time = row['datetime']
                pe_points = entry_price - exit_price
                exit_remark = 'Target Hit'
                in_trade_pe = False

        if pe_points:
            # print(exit_remark)
            qty = portfolio_ * lev_ / pe_strike
            slippages = (entry_price + exit_price) * slippage_
            trade = {
                'Strike': pe_strike,
                'Option Type': 'PE',
                'Expiry': expiry,
                'Portfolio': portfolio_,
                'Entry Time': entry_time,
                'Entry Price': entry_price,
                'Exit Time': exit_time,
                'Exit Price': exit_price,
                'Remark': exit_remark,
                'Points': pe_points,
                'Qty': qty,
                'PnL': pe_points * qty,
                'Slippages': slippages,
                'PnL w cs': (pe_points - slippages) * qty,
                'ROI%': (pe_points - slippages) * qty * 100 / portfolio_,
            }
            # print(trade)
            tradebook.append(trade)
            pe_points = 0
            exit_remark = None

    # Append today's trades to the overall tradebook
    tradebook_df = pd.DataFrame(tradebook)
    
    return tradebook_df

In [57]:
async def trade(df, tf, i1, j1):

    if tf == "10m":
        ofs = "5m"
    elif tf == "30m":
        ofs = "15m"
    else:
        ofs = "0m"
        
    # combined_trades_ce = pd.DataFrame()
    # combined_trades_pe = pd.DataFrame()
    total_trades = pd.DataFrame()

    start_date = df.iloc[0]['datetime'].date()
    end_date = df.iloc[-1]['datetime'].date()
    # print(start_date, end_date)
    current_date = start_date
    i = 1
    while current_date <= end_date:
        spot_row = df[df['datetime'].dt.date == current_date]
        spot_open = spot_row['open'].iloc[0] if len(spot_row) > 0 else 0
        if spot_open == 0:
            current_date += dt.timedelta(days=1)
        else:
            spot_atm = int(round(spot_open / spread_) * spread_)
            # print(spot_open, spot_atm)
            # break
            current_expiry = await get_expiry(current_date, index_)
            # print(current_date)
            # break
    
            ce_df = await fetch_data(
                index=index_,
                start_date=current_date,
                end_date=current_date,
                start_time=dt.time(9, 15),
                end_time=dt.time(15, 30),
                expiry=current_expiry,
                strike=spot_atm,
                asset_class="C",
            )
            # print(ce_df)
            if not isinstance(ce_df, str) and ce_df is not None:
                ce_df = ce_df.select(["datetime", "o", "h", "l", "c", "v"])
                ce_df = resample(ce_df, tf, offset=ofs)
                ce_df_pandas = ce_df.to_pandas()
                ce_df_pandas = ce_df_pandas[~(ce_df_pandas['datetime'].dt.time == pd.to_datetime('15:30').time())]
                ce_df = generate_reversal_signals(ce_df_pandas, i1, j1)
                # print(spot_atm, 'CE DF :\n')
                # print(ce_df.to_string())
    
            else:
                current_date += dt.timedelta(days=1)
                continue
    
            pe_df = await fetch_data(
                index=index_,
                start_date=current_date,
                end_date=current_date,
                start_time=dt.time(9, 15),
                end_time=dt.time(15, 30),
                expiry=current_expiry,
                strike=spot_atm,
                asset_class="P",
            )
            # print(pe_df)
            if not isinstance(pe_df, str) and pe_df is not None:
                pe_df = pe_df.select(["datetime", "o", "h", "l", "c", "v"])
                pe_df = resample(pe_df, tf, offset=ofs)
                pe_df_pandas = pe_df.to_pandas()
                pe_df_pandas = pe_df_pandas[~(pe_df_pandas['datetime'].dt.time == pd.to_datetime('15:30').time())]
                pe_df = generate_reversal_signals(pe_df_pandas, i1, j1)
                # print(spot_atm, 'PE DF :\n')
                # print(pe_df.to_string())
    
            else:
                current_date += dt.timedelta(days=1)
                continue
    
            # print(ce_df.to_string(), pe_df.to_string())

            tb = await take_trade(ce_df, pe_df, spot_atm, spot_atm, current_expiry)
            total_trades = pd.concat([total_trades, tb], ignore_index=True)
            current_date += dt.timedelta(days=1)
            # if i == 5:
            #     break
            # i+=1
    return total_trades
            # break

In [58]:
TB = await trade(bnf.to_pandas(), '5m', 5, 25)

In [59]:
TB

Strike Option Type      Expiry  Portfolio          Entry Time  \
0      10850          CE  2019-01-31   10000000 2019-01-25 09:35:00   
1      10850          PE  2019-01-31   10000000 2019-01-25 09:20:00   
2      10850          PE  2019-01-31   10000000 2019-01-25 13:50:00   
3      10850          PE  2019-01-31   10000000 2019-01-25 14:25:00   
4      10800          CE  2019-01-31   10000000 2019-01-28 09:25:00   
5      10800          PE  2019-01-31   10000000 2019-01-28 09:55:00   
6      10800          PE  2019-01-31   10000000 2019-01-28 15:25:00   
7      10650          CE  2019-01-31   10000000 2019-01-29 09:25:00   
8      10650          PE  2019-01-31   10000000 2019-01-29 09:25:00   
9      10700          CE  2019-01-31   10000000 2019-01-30 09:20:00   
10     10700          CE  2019-01-31   10000000 2019-01-30 15:25:00   
11     10700          PE  2019-01-31   10000000 2019-01-30 09:25:00   
12     10700          PE  2019-01-31   10000000 2019-01-30 10:45:00   
13     10700          CE  2019-01-31   10000000 2019-01-31 09:20:00   
14     10700          CE  2019-01-31   10000000 2019-01-31 10:50:00   
15     10700          CE  2019-01-31   10000000 2019-01-31 11:35:00   
16     10700          CE  2019-01-31   10000000 2019-01-31 13:25:00   
17     10700          CE  2019-01-31   10000000 2019-01-31 15:05:00   
18     10700          PE  2019-01-31   10000000 2019-01-31 09:20:00   
19     10700          PE  2019-01-31   10000000 2019-01-31 09:55:00   
20     10700          PE  2019-01-31   10000000 2019-01-31 14:25:00   
21     10700          PE  2019-01-31   10000000 2019-01-31 14:35:00   
22     10700          PE  2019-01-31   10000000 2019-01-31 14:50:00   
23     10700          PE  2019-01-31   10000000 2019-01-31 15:05:00   
24     10950          CE  2019-02-14   10000000 2019-02-11 09:20:00   
25     10950          PE  2019-02-14   10000000 2019-02-11 09:35:00   
26     10950          PE  2019-02-14   10000000 2019-02-11 15:25:00   
27     10900          CE  2019-02-14   10000000 2019-02-12 09:25:00   
28     10900          CE  2019-02-14   10000000 2019-02-12 15:25:00   
29     10900          PE  2019-02-14   10000000 2019-02-12 09:20:00   
30     10900          PE  2019-02-14   10000000 2019-02-12 14:55:00   
31     10850          CE  2019-02-14   10000000 2019-02-13 09:20:00   
32     10850          CE  2019-02-14   10000000 2019-02-13 15:25:00   
33     10850          PE  2019-02-14   10000000 2019-02-13 09:25:00   
34     10850          PE  2019-02-14   10000000 2019-02-13 13:50:00   
35     10800          CE  2019-02-14   10000000 2019-02-14 09:20:00   
36     10800          PE  2019-02-14   10000000 2019-02-14 09:25:00   
37     10800          PE  2019-02-14   10000000 2019-02-14 13:45:00   
38     10800          PE  2019-02-14   10000000 2019-02-14 15:25:00   
39     10800          CE  2019-02-21   10000000 2019-02-15 09:20:00   
40     10800          CE  2019-02-21   10000000 2019-02-15 15:25:00   
41     10800          PE  2019-02-21   10000000 2019-02-15 09:25:00   
42     10800          PE  2019-02-21   10000000 2019-02-15 12:25:00   
43     10750          CE  2019-02-21   10000000 2019-02-18 09:20:00   
44     10750          CE  2019-02-21   10000000 2019-02-18 15:25:00   
45     10750          PE  2019-02-21   10000000 2019-02-18 10:00:00   
46     10650          CE  2019-02-21   10000000 2019-02-19 09:25:00   
47     10650          PE  2019-02-21   10000000 2019-02-19 09:25:00   
48     10650          PE  2019-02-21   10000000 2019-02-19 15:25:00   
49     10650          CE  2019-02-21   10000000 2019-02-20 09:45:00   
50     10650          CE  2019-02-21   10000000 2019-02-20 15:15:00   
51     10650          PE  2019-02-21   10000000 2019-02-20 09:20:00   
52     10750          CE  2019-02-21   10000000 2019-02-21 09:25:00   
53     10750          CE  2019-02-21   10000000 2019-02-21 11:35:00   
54     10750          CE  2019-02-21   10000000 2019-02-21 13:15:00   
55     10750          CE  2019

In [60]:
TB['ROI%'].sum()

-199.42355099524332

In [61]:
def generate_stats(tb_expiry):
    stats_df8 = pd.DataFrame(
        index=range(2019, 2025),
        columns=[
            "Total ROI",
            "Total Trades",
            "Win Rate",
            "Avg Profit% per Trade",
            "Avg Loss% per Trade",
            "Max Drawdown",
            "ROI/DD Ratio",
            # "Variation",
        ],
    )
    combined_df_sorted = tb_expiry
    # combined_df_sorted = tb_expiry_ce
    # combined_df_sorted = tb_expiry_pe
    
    # Iterate over each year
    for year in range(2019, 2025):
        # Filter trades for the current year
        year_trades = combined_df_sorted[(combined_df_sorted["Trade Year"] == year)]
    
        # Calculate total ROI
        total_roi = year_trades["ROI%"].sum()
    
        # Calculate total number of trades
        total_trades = len(year_trades)
    
        # Calculate win rate
        win_rate = (year_trades["ROI%"] > 0).mean() * 100
    
        # Calculate average profit per trade
        avg_profit = year_trades[year_trades["ROI%"] > 0]["ROI%"].mean()
    
        # Calculate average loss per trade
        avg_loss = year_trades[year_trades["ROI%"] < 0]["ROI%"].mean()
    
        # Calculate maximum drawdown
        max_drawdown = (
            year_trades["ROI%"].cumsum() - year_trades["ROI%"].cumsum().cummax()
        ).min()
    
        # Calculate ROI/DD ratio
        roi_dd_ratio = total_roi / abs(max_drawdown)

        # variation = f' {signal_ma},{num_candels}'
    
        # Store the statistics in the DataFrame
        stats_df8.loc[year] = [
            total_roi,
            total_trades,
            win_rate,
            avg_profit,
            avg_loss,
            max_drawdown,
            roi_dd_ratio,
            # variation,
        ]
    
    # Calculate overall statistics
    overall_total_roi = stats_df8["Total ROI"].sum()
    overall_total_trades = stats_df8["Total Trades"].sum()
    overall_win_rate = (combined_df_sorted["ROI%"] > 0).mean() * 100
    overall_avg_profit = combined_df_sorted[combined_df_sorted["ROI%"] > 0]["ROI%"].mean()
    overall_avg_loss = combined_df_sorted[combined_df_sorted["ROI%"] < 0]["ROI%"].mean()
    overall_max_drawdown = (
        combined_df_sorted["ROI%"].cumsum() - combined_df_sorted["ROI%"].cumsum().cummax()
    ).min()
    overall_roi_dd_ratio = overall_total_roi / abs(overall_max_drawdown)
    # overall_variation = variation
    
    # Store the overall statistics in the DataFrame
    stats_df8.loc["Overall"] = [
        overall_total_roi,
        overall_total_trades,
        overall_win_rate,
        overall_avg_profit,
        overall_avg_loss,
        overall_max_drawdown,
        overall_roi_dd_ratio,
        # overall_variation,
    ]
    return {overall_roi_dd_ratio : stats_df8}

In [62]:
TB['Entry Time'] = pd.to_datetime(TB['Entry Time'])
TB['Trade Year'] = TB['Entry Time'].dt.year
stats = generate_stats(TB)
for overall_roi_dd_ratio, stats_df in stats.items():
    if overall_roi_dd_ratio is not None and overall_roi_dd_ratio > -2:
        # print("Overall Combined")
        print(stats_df.to_string())
        # stats_dictionary[overall_roi_dd_ratio] = stats_df

        Total ROI Total Trades Win Rate Avg Profit% per Trade Avg Loss% per Trade Max Drawdown ROI/DD Ratio
2019     -34.3701          875  45.3714                1.1876             -1.0582     -58.5288      -0.5872
2020     -33.6323         1008  45.4365                1.9470             -1.6824     -72.1771      -0.4660
2021     -44.0542          957  47.0219                1.2508             -1.1971     -56.2809      -0.7828
2022     -46.9387          941  45.3773                1.2846             -1.1585     -54.5474      -0.8605
2023     -12.6004          934  48.3940                0.8268             -0.8015     -20.6940      -0.6089
2024     -27.8279          409  46.2103                1.2674             -1.2153     -43.6054      -0.6382
Overall -199.4236    5124.0000  46.3115                1.3012             -1.1949    -217.6460      -0.9163


In [55]:
# # atr_window
# # ma_window
# # atr_multiplier

# stats_dictionary = {}
# tf_list = ['3m', '5m', '10m']
# atr_multiplier = [1.25, 1.4, 1.5, 1.75, 2, 2.25, 2.5]

# for i in range(4, 17):
#     for j in range(5, 17):
#         for k in atr_multiplier:
#             for tf in tf_list:
#                 print(i, j, k, tf)
#                 tb = await trade(bnf.to_pandas(), tf, i, j, k)
#                 if len(tb) > 0:
#                     tb['Entry Time'] = pd.to_datetime(tb['Entry Time'])
#                     tb['Trade Year'] = tb['Entry Time'].dt.year
#                     stats = generate_stats(tb)
#                     for overall_roi_dd_ratio, stats_df in stats.items():
#                         # if overall_roi_dd_ratio is not None and overall_roi_dd_ratio > -1:
#                             # print("Overall Combined")
#                         print(stats_df.to_string())
#                         stats_dictionary[overall_roi_dd_ratio] = stats_df